In [1]:
import mbuild as mb 

import numpy as np
import matplotlib.pyplot as plt 


import sys
sys.path.insert(1, '../surface_coatings/')
import surface_coatings
from surface_coatings import *
from mbuild.lib.atoms import H
from mbuild.lib.moieties import Silane, CH2
from foyer import Forcefield
from surface_coatings.surfaces import SilicaInterfaceCarve

from gmso.external.convert_mbuild import to_mbuild

from utils.index_groups import generate_index_groups

import networkx as nx

import textwrap

/Users/kieran/opt/miniconda3/envs/pmpc/lib/python3.8/site-packages/mbuild/utils/decorators.py:134: Warning: freud_generate_bonds is an experimental feature and is not subject to follow standard deprecation cycles. Use at your own risk! 
  warn(


In [2]:
def combine_forcefield():
    from collections import Counter
    added = []
    with open('utils/charge_neutral_oplsaa_imodels_v2.xml', "w") as f2:
        with open('utils/charge_neutral_oplsaa_imodels.xml', "r") as f:
            lines = f.readlines()
            removed_lines = [l.replace(" ","") for l in lines]
            c = Counter(removed_lines)
            for i, l in enumerate(removed_lines):
                if (c[l] == 1) or (l not in added):
                    if l not in added:
                        added.append(l)
                    f2.write(lines[i])
                else:
                    print(l)
            f.close()
        f2.close()
        
def dihedral_to_RB(k1,k2,k3,k4):
    c0 = k2+.5*(k1+k3)
    c1 = .5*(-k1+3*k3)
    c2 = -k2+4*k4
    c3 = -2*k3
    c4 = -4*k4
    c5 = 0
    return c0, c1, c2, c3, c4, c5
print(dihedral_to_RB(-4.309520, -0.654796, 0.658980, 0.000000))

def combine_ligpargen_forcefield():
  # mb.load('CC(C)(CCCCC[SiH](O)O)C(=O)OCCO[P]([O-])(=O)OCC[N+](C)(C)C', smiles=True).visualize()

  with open('/Users/kieran/pmpc/utils/mpc_methyl_ligpargen.xml') as f:
    lines = f.readlines()
    f.close()

  lines_b = lines[68:193] #lines with graph info
  lines_a = lines[2:65] 
  atoms = [l for l in lines if 'Atom' and 'type' in l ]
  bonds = [l for l in lines_b if 'Bond' in l ]
  opls2class = {a.split('"')[1]: a.split('"')[3] for i, a in enumerate(lines_a)}

  index2atoms = {i: a.split('"')[1] for i, a in enumerate(atoms)}
  atoms2opls = {a.split('"')[1]:a.split('"')[3] for i, a in enumerate(atoms)}

  connections = []
  for b in bonds:
    c = tuple([int(s) for s in b.split('"') if s.isdigit()])
    connections.append(c)

  G = nx.Graph()
  for b in connections:
    G.add_edge(index2atoms[b[0]], index2atoms[b[1]])
  plt.figure(figsize=(12,12))
  nx.draw(G, with_labels=True)
  print('We need {}, {}, {}, {}'.format(opls2class[atoms2opls['C0C']],opls2class[atoms2opls['C01']],opls2class[atoms2opls['C03']],opls2class[atoms2opls['C04']]))

(-2.480066, 3.14323, 0.654796, -1.31796, -0.0, 0)


In [3]:
import panedr

data = panedr.edr_to_df('em.edr')
data.head()

FileNotFoundError: [Errno 2] No such file or directory: 'em.edr'

In [42]:
surface = SilicaInterfaceCarve()
chain = SilanePolymer(n=2)
surface.periodicity = (True, True, True)
# for i, p in enumerate(chain):
#     if p.name == 'Si':
#         start = i
# i = 0
# while True:
#     try:
#         chain[start+5+i].name = chain[start+5+i].name + '_K'
#         i += 1
#     except:
#         break

monolayer = Monolayer(surface=mb.clone(surface), 
                      chains=mb.clone(chain), 
                      n_chains=10, 
                      tile_x=1, 
                      tile_y=1,
                      rotate_chains=False)
dual_monolayer = DualMonolayer(top=mb.clone(monolayer),
                               bottom=mb.clone(monolayer),
                               separation=3,
                               shift=False)
solvated_dual_monolayer = SolvatedDualMonolayer(dual_monolayer=mb.clone(dual_monolayer))
solvated_dual_monolayer.periodicity = (True, True, True)


solvated_dual_monolayer.box = mb.Box(lengths=[5,5,50])
for p in solvated_dual_monolayer.particles():
    if p.name == 'O_Surface':
        p.name = 'O_S'

In [43]:
oplsaa = Forcefield(forcefield_files="./utils/charge_neutral_oplsaa_imodels_v2.xml")
typed_monolayer = oplsaa.apply(solvated_dual_monolayer,  verbose=True)
# for a in solvated_dual_monolayer.particles():
#     if '_K' in a.name:
#         a.name = a.name[:-2] 
# for a in typed_monolayer.atoms:
#     if '_K' in a.name:
#         a.charge = 0
#         a.name = a.name[:-2] 
typed_monolayer.save('solvated_dual_monolayer.top', overwrite=True, combine="all")

In [44]:
gmso_solvated = solvated_dual_monolayer.to_gmso()
gmso_solvated.save('solvated_dual_monolayer.gro',overwrite=True)

/Users/kieran/opt/miniconda3/envs/pmpc/lib/python3.8/site-packages/gmso/core/topology.py:664: UserWarning: Non-parametrized site detected <Atom O, label: None id: 140580259190576>
  warnings.warn("Non-parametrized site detected {}".format(site))
/Users/kieran/opt/miniconda3/envs/pmpc/lib/python3.8/site-packages/gmso/core/topology.py:664: UserWarning: Non-parametrized site detected <Atom O, label: None id: 140580259190048>
  warnings.warn("Non-parametrized site detected {}".format(site))
/Users/kieran/opt/miniconda3/envs/pmpc/lib/python3.8/site-packages/gmso/core/topology.py:664: UserWarning: Non-parametrized site detected <Atom O, label: None id: 140580259189280>
  warnings.warn("Non-parametrized site detected {}".format(site))
/Users/kieran/opt/miniconda3/envs/pmpc/lib/python3.8/site-packages/gmso/core/topology.py:664: UserWarning: Non-parametrized site detected <Atom O, label: None id: 140580259189904>
  warnings.warn("Non-parametrized site detected {}".format(site))
/Users/kieran/op

In [45]:
from mbuild.formats.lammpsdata import write_lammpsdata

# solvated_dual_monolayer.box = mb.Box(lengths=[5,5,50])
write_lammpsdata(filename='init.lammps', structure=typed_monolayer,use_rb_torsions = True)

No urey bradley terms detected, will use angle_style harmonic
RB Torsions detected, will use dihedral_style opls


In [46]:
def generate_index_groups(system, freeze_thickness=0.5):
    bounding_box = system.get_boundingbox().lengths
    z_poses = [p.pos[2] for p in system.particles()]
    bot_of_box = min(z_poses)
    top_of_box =  max(z_poses)
    middle = bounding_box[2]/2

    bottom_frozen = []
    top_frozen = []
    surfaces = []
    chains = []
    for i, particle in enumerate(system.particles()):
        z = particle.pos[2]
        ancestors = [ancestor.name for ancestor in particle.ancestors()]
        if 'SilanePolymer' in ancestors or 'Silane' in ancestors:
            chains.append(i + 1)
        else:
            surfaces.append(i + 1)
            if  z < bot_of_box + freeze_thickness:
                bottom_frozen.append(i + 1)
            if z > top_of_box - freeze_thickness:
                top_frozen.append(i+1)

    bottom_frozen = np.asarray(bottom_frozen)
    print('bottom_frozen: {}'.format(len(bottom_frozen)))

    top_frozen = np.asarray(top_frozen)
    print('top_frozen: {}'.format(len(top_frozen)))

    surfaces = np.asarray(surfaces)
    print('surfaces: {}'.format(len(surfaces)))

    chains = np.array(chains)
    print('chains: {}'.format(len(chains)))

    system = np.hstack((chains, surfaces))
    print('system: {}'.format(len(system)))

    index_groups = {'System': system,
                    'top_frozen': top_frozen,
                    'bottom_frozen': bottom_frozen,
                    'surfaces': surfaces,
                    'chains': chains}

    return index_groups
    
def write_monolayer_ndx(rigid_groups, filename):
    with open(filename, 'w') as f:
        for name, indices in rigid_groups.items():
            f.write('[ {name} ]\n'.format(name=name))
            atoms = '{}\n'.format(' '.join(str(x) for x in indices))
            f.write(textwrap.fill(atoms, 80))
            f.write('\n')

In [47]:
index_groups = generate_index_groups(system=solvated_dual_monolayer, freeze_thickness=0.5)
write_monolayer_ndx(rigid_groups=index_groups, filename='init.ndx')

bottom_frozen: 629
top_frozen: 629
surfaces: 6804
chains: 2040
system: 8844


In [48]:
!gmx grompp -f /Users/kieran/terminal_groups_mixed/src/util/mdp_files/em.mdp -c solvated_dual_monolayer.gro -p solvated_dual_monolayer.top -n init.ndx -o em.tpr -maxwarn 5

                :-) GROMACS - gmx grompp, 2022.1-conda_forge (-:

Executable:   /Users/kieran/opt/miniconda3/envs/pmpc/bin.AVX2_256/gmx
Data prefix:  /Users/kieran/opt/miniconda3/envs/pmpc
Working dir:  /Users/kieran/pmpc
Command line:
  gmx grompp -f /Users/kieran/terminal_groups_mixed/src/util/mdp_files/em.mdp -c solvated_dual_monolayer.gro -p solvated_dual_monolayer.top -n init.ndx -o em.tpr -maxwarn 5

Ignoring obsolete mdp entry 'ns_type'

NOTE 1 [file /Users/kieran/terminal_groups_mixed/src/util/mdp_files/em.mdp]:
  With Verlet lists the optimal nstlist is >= 10, with GPUs >= 20. Note
  that with the Verlet scheme, nstlist has no effect on the accuracy of
  your simulation.


WARNING 1 [file /Users/kieran/terminal_groups_mixed/src/util/mdp_files/em.mdp]:
  With PME and ewald_geometry = 3dc you should use pbc = xy

Setting the LD random seed to -279650313

Generated 465 of the 465 non-bonded parameter combinations
Generating 1-4 interactions: fudge = 0.5

Generated 465 of the 465 

In [49]:
!lmp_serial -in /Users/kieran/pmpc/in.minimize -log minimize.log

LAMMPS (29 Sep 2021 - Update 3)
Reading data file ...
  orthogonal box = (0.0000000 0.0000000 0.0000000) to (50.000000 50.000000 50.000000)
  1 by 1 by 1 MPI processor grid
  reading atoms ...
  5593 atoms
ERROR: Did not assign all atoms correctly (src/read_data.cpp:1256)
Last command: read_data	/Users/kieran/pmpc/init.lammps


In [13]:
!gmx_mpi trjconv -s solvated_dual_monolayer.gro -f minimize.xtc -o minimized.gro -b 1.0 -e 1.0

                     :-) GROMACS - gmx trjconv, 2018.1 (-:

                            GROMACS is written by:
     Emile Apol      Rossen Apostolov      Paul Bauer     Herman J.C. Berendsen
    Par Bjelkmar    Aldert van Buuren   Rudi van Drunen     Anton Feenstra  
  Gerrit Groenhof    Aleksei Iupinov   Christoph Junghans   Anca Hamuraru   
 Vincent Hindriksen Dimitrios Karkoulis    Peter Kasson        Jiri Kraus    
  Carsten Kutzner      Per Larsson      Justin A. Lemkul    Viveca Lindahl  
  Magnus Lundborg   Pieter Meulenhoff    Erik Marklund      Teemu Murtola   
    Szilard Pall       Sander Pronk      Roland Schulz     Alexey Shvetsov  
   Michael Shirts     Alfons Sijbers     Peter Tieleman    Teemu Virolainen 
 Christian Wennberg    Maarten Wolf   
                           and the project leaders:
        Mark Abraham, Berk Hess, Erik Lindahl, and David van der Spoel

Copyright (c) 1991-2000, University of Groningen, The Netherlands.
Copyright (c) 2001-2017, The GROMACS de

In [21]:
with open('minimized.gro', 'r') as f:
    lines = f.readlines()
    f.close()
with open('minimized_corrected.gro', 'w') as f:
    f.write(lines[0])
    f.write(lines[1])
    for l in lines[2:-1]:
        if len(l.split())!= 6:
        # if l[14].isalpha():
            l = list(l)
            l[10], l[14] = l[14], l[10]
            l = ''.join(l)
        f.write(l)
    f.write(lines[-1])
    # 1X    H    11104   2.029   4.827   4.025

In [68]:
# !gmx grompp -f nvt.mdp -c minimized.gro -p solvated_dual_monolayer.top -n init.ndx -o equalibrate.tpr -maxwarn 5
!gmx mdrun -v -deffnm equalibrate -s equalibrate.tpr -c minimized.gro

                :-) GROMACS - gmx mdrun, 2022.1-conda_forge (-:

Executable:   /Users/kieran/opt/miniconda3/envs/pmpc/bin.AVX2_256/gmx
Data prefix:  /Users/kieran/opt/miniconda3/envs/pmpc
Working dir:  /Users/kieran/pmpc
Command line:
  gmx mdrun -v -deffnm equalibrate -s equalibrate.tpr -c minimized.gro


Back Off! I just backed up equalibrate.log to ./#equalibrate.log.1#
Reading file equalibrate.tpr, VERSION 2022.1-conda_forge (single precision)
Changing nstlist from 10 to 100, rlist from 1 to 1

NOTE: Periodic molecules are present in this system. Because of this, the domain decomposition algorithm cannot easily determine the minimum cell size that it requires for treating bonded interactions. Instead, domain decomposition will assume that half the non-bonded cut-off will be a suitable lower bound.
Using 1 MPI thread
Using 4 OpenMP threads 


Back Off! I just backed up equalibrate.xtc to ./#equalibrate.xtc.1#

Back Off! I just backed up equalibrate.trr to ./#equalibrate.trr.1#

Back

In [41]:
import mosdef_cassandra as mc
import unyt as u

# Create box and species list
box_list = [solvated_dual_monolayer.get_boundingbox()]
species_list = [typed_monolayer]

mols_to_add = [[100]]

system = mc.System(box_list, species_list, mols_to_add=mols_to_add)
moveset = mc.MoveSet("gcmc", species_list)

default_args = {
    "chemical_potentials": [-35.0 * (u.kJ / u.mol)],
    "prop_freq": 100,
}

# Combine default/custom args and override default
custom_args = {**default_args}

mc.run(
    system=system,
    moveset=moveset,
    run_type="equilibration",
    run_length=1000,
    temperature=300.0 * u.K,
    **custom_args,
)

ERROR: Constructing component 'eq_calc_bound_length' from data=None failed:
    KeyboardInterrupt:


KeyboardInterrupt: 

In [ ]:
import foyer
import mbuild as mb
import mosdef_cassandra as mc
import unyt as u
from mbuild.formats.xyz import read_xyz
from pymbar.timeseries import detectEquilibration

from reproducibility_project.src.molecules.system_builder import (
    construct_system,
    get_molecule,
)
from reproducibility_project.src.utils.forcefields import load_ff

molecule = job.sp.molecule

compound = get_molecule(job.sp)

ensemble = job.sp.ensemble

cass_ensembles = {
    "NPT": "npt",
    "GEMC-NVT": "gemc",
}

cass_cutoffs = {
    ("hard", "None"): "cut",
    ("hard", "energy_pressure"): "cut_tail",
    ("shift", "None"): "cut_shift",
}
cutoff_style = cass_cutoffs[
    (job.sp.cutoff_style, job.sp.long_range_correction)
]

Nliq = job.sp.N_liquid
if ensemble == "GEMC-NVT":
    Nvap = job.sp.N_vap
else:
    Nvap = 0

N = Nliq + Nvap

Nlist = [[Nliq]]

equil_length = 40000
prod_length = 120000

filled_boxes = construct_system(job.sp)

liqbox_filled = filled_boxes[0]
if ensemble == "GEMC-NVT":
    vapbox_filled = filled_boxes[1]
    Nlist.append([Nvap])

ffname = job.sp.forcefield_name
ff = load_ff(ffname)
structure = ff.apply(compound)

if any([abs(a.charge) > 0.0 for a in structure.atoms]):
    charge_style = "ewald"
else:
    charge_style = "none"

Tmelt = 1000.0 * u.K

T = job.sp.temperature * u.K
P = job.sp.pressure * u.kPa

species_list = [structure]
cutoff = job.sp.r_cut * u.nm

seedslist = [
    [7860904, 8601355],
    [5793508, 4173039],
    [4420642, 8720464],
    [8120272, 5850411],
    [7616664, 1492980],
    [6844679, 6087693],
    [2175335, 1317929],
    [9725500, 6331893],
    [4247127, 1385831],
    [2946981, 9870819],
    [8434295, 8017520],
    [8424221, 4595446],
    [8870203, 3009902],
    [4564019, 4788324],
    [3927152, 2536489],
    [3375750, 1798462],
]

seeds = seedslist[job.sp.replica]
cbmc_n_ins = 12
cbmc_n_dihed = 50

prop_freq = 10
coord_freq = 10
if ff.combining_rule == "geometric":
    comb_rule = "geometric"
else:
    comb_rule = "lb"

proplist = [
    "energy_total",
    "volume",
    "nmols",
    "pressure",
    "density",
    "mass_density",
    "energy_angle",
    "energy_dihedral",
    "energy_intravdw",
    "energy_intraq",
    "energy_inter",
    "energy_intervdw",
    "energy_lrc",
    "energy_interq",
    "energy_recip",
    "energy_self",
    "enthalpy",
]

meltsystem_liq = mc.System([liqbox_filled], species_list, [[Nliq]])

p_volume = 0.01
p_translate = 0.0
p_rotate = 0.0
p_regrow = 0.0
p_swap = 0.0

if molecule == "methaneUA":
    if ensemble == "NPT":
        p_translate = 0.99
    else:
        p_translate = 0.7
        p_swap = 0.29
elif "pentaneUA" in molecule and ensemble == "GEMC-NVT":
    p_swap = 0.2
    p_translate = 0.27
    p_rotate = 0.26
    p_regrow = 0.26
elif molecule == "waterSPCE" or molecule == "benzeneUA":
    p_translate = 0.49
    p_rotate = 0.5
else:
    p_translate = 0.33
    p_rotate = 0.33
    p_regrow = 0.33

nvtmoves = mc.MoveSet("nvt", species_list)
nvtmoves.prob_rotate = p_rotate
nvtmoves.prob_translate = p_translate
nvtmoves.prob_regrow = p_regrow

moveset = mc.MoveSet(cass_ensembles[ensemble], species_list)
moveset.prob_volume = p_volume
moveset.prob_translate = p_translate
moveset.prob_rotate = p_rotate
moveset.prob_regrow = p_regrow
moveset.cbmc_n_ins = cbmc_n_ins
moveset.cbmc_n_dihed = cbmc_n_dihed

with job:
    if not check_complete("nvt_melt"):
        mc.run(
            system=meltsystem_liq,
            moveset=nvtmoves,
            run_type="equilibration",
            run_length=5000,
            temperature=Tmelt,
            properties=proplist,
            cutoff_style=cutoff_style,
            charge_style=charge_style,
            vdw_cutoff=cutoff,
            charge_cutoff=cutoff,
            mixing_rule=comb_rule,
            run_name="nvt_melt",
            prop_freq=prop_freq,
            coord_freq=5000,
            units="sweeps",
            steps_per_sweep=Nliq,
            seeds=seeds,
        )

    nvtendbox_liq = read_xyz("nvt_melt.out.xyz")

    nvtendbox_liq.box = liqbox_filled.box

    nvtsystem_liq = mc.System([nvtendbox_liq], species_list, [[Nliq]])

    if not check_complete("nvt_equil"):
        mc.run(
            system=nvtsystem_liq,
            moveset=nvtmoves,
            run_type="equilibration",
            run_length=5000,
            temperature=T,
            properties=proplist,
            cutoff_style=cutoff_style,
            charge_style=charge_style,
            vdw_cutoff=cutoff,
            charge_cutoff=cutoff,
            mixing_rule=comb_rule,
            run_name="nvt_equil",
            prop_freq=prop_freq,
            coord_freq=5000,
            units="sweeps",
            steps_per_sweep=Nliq,
            seeds=seeds,
        )

    nvtendbox_liq = read_xyz("nvt_equil.out.xyz")

    nvtendbox_liq.box = liqbox_filled.box
    boxlist = [nvtendbox_liq]

    if ensemble == "GEMC-NVT":
        meltsystem_vap = mc.System([vapbox_filled], species_list, [[Nvap]])
        if not check_complete("nvt_melt_vap"):
            mc.run(
                system=meltsystem_vap,
                moveset=nvtmoves,
                run_type="equilibration",
                run_length=5000,
                temperature=Tmelt,
                properties=proplist,
                cutoff_style=cutoff_style,
                charge_style=charge_style,
                vdw_cutoff=cutoff,
                charge_cutoff=cutoff,
                mixing_rule=comb_rule,
                run_name="nvt_melt_vap",
                prop_freq=prop_freq,
                coord_freq=5000,
                units="sweeps",
                steps_per_sweep=Nvap,
                seeds=seeds,
            )
        meltendbox_vap = read_xyz("nvt_melt_vap.out.xyz")

        meltendbox_vap.box = vapbox_filled.box
        nvtsystem_vap = mc.System([meltendbox_vap], species_list, [[Nvap]])
        if not check_complete("nvt_equil_vap"):
            mc.run(
                system=nvtsystem_vap,
                moveset=nvtmoves,
                run_type="equilibration",
                run_length=5000,
                temperature=T,
                properties=proplist,
                cutoff_style=cutoff_style,
                charge_style=charge_style,
                vdw_cutoff=cutoff,
                charge_cutoff=cutoff,
                mixing_rule=comb_rule,
                run_name="nvt_equil_vap",
                prop_freq=prop_freq,
                coord_freq=5000,
                units="sweeps",
                steps_per_sweep=Nvap,
                seeds=seeds,
            )
        nvtendbox_vap = read_xyz("nvt_equil_vap.out.xyz")

        nvtendbox_vap.box = vapbox_filled.box
        boxlist.append(nvtendbox_vap)
        moveset.prob_swap = p_swap

    system = mc.System(boxlist, species_list, Nlist)

    l_equil = False
    cycles_done = 0

    this_run = "equil_" + str(cycles_done)
    if not has_checkpoint(this_run):
        mc.run(
            system=system,
            moveset=moveset,
            run_type="equilibration",
            run_length=equil_length,
            temperature=T,
            pressure=P,  # this line is ignored if ensemble isn't NPT
            properties=proplist,
            cutoff_style=cutoff_style,
            charge_style=charge_style,
            vdw_cutoff=cutoff,
            charge_cutoff=cutoff,
            mixing_rule=comb_rule,
            run_name=this_run,
            prop_freq=prop_freq,
            coord_freq=coord_freq,
            units="sweeps",
            steps_per_sweep=N,
            seeds=seeds,
        )
    elif not check_complete(this_run):
        mc.restart(
            restart_from=get_last_checkpoint(this_run),
        )

    cycles_done += equil_length

    if ensemble == "GEMC-NVT":
        prpsuffix_liq = ".out.box1.prp"
        prpsuffix_vap = ".out.box2.prp"
        xyzsuffix_liq = ".out.box1.xyz"
        xyzsuffix_vap = ".out.box2.xyz"
        Hsuffix_liq = ".out.box1.H"
        Hsuffix_vap = ".out.box2.H"
        merge_restart_prp(this_run + prpsuffix_vap)
    else:
        prpsuffix_liq = ".out.prp"
        xyzsuffix_liq = ".out.xyz"
        Hsuffix_liq = ".out.H"
    merge_restart_prp(this_run + prpsuffix_liq)

    t, g, Neff_max = detectEquilibration(
        np.loadtxt(this_run + prpsuffix_liq, usecols=5)
    )

    if ensemble == "GEMC-NVT":
        tvap, gvap, Neff_max_vap = detectEquilibration(
            np.loadtxt(this_run + prpsuffix_vap, usecols=5)
        )
        t = max(t, tvap)
    prior_run = this_run

    for i in range(2):
        if t >= equil_length * 3 / (prop_freq * 4):
            this_run = "equil_" + str(cycles_done)
            if not has_checkpoint(this_run):
                mc.restart(
                    restart_from=prior_run,
                    run_name=this_run,
                    run_type="equilibration",
                    total_run_length=cycles_done + equil_length,
                )
            elif not check_complete(this_run):
                mc.restart(
                    restart_from=get_last_checkpoint(this_run),
                )
            cycles_done += equil_length
            merge_restart_prp(this_run + prpsuffix_liq)
            t, g, Neff_max = detectEquilibration(
                np.loadtxt(this_run + prpsuffix_liq, usecols=5)
            )

            if ensemble == "GEMC-NVT":
                merge_restart_prp(this_run + prpsuffix_vap)
                tvap, gvap, Neff_max_vap = detectEquilibration(
                    np.loadtxt(this_run + prpsuffix_vap, usecols=5)
                )
                t = max(t, tvap)

            for rmtgt in list(Path(".").glob("equil_*.[xH]*")):
                os.remove(rmtgt)
            prior_run = this_run

        else:
            break

    if has_checkpoint("prod"):
        mc.restart(
            restart_from=get_last_checkpoint("prod"),
        )
    else:
        mc.restart(
            restart_from=prior_run,
            run_name="prod",
            run_type="production",
            total_run_length=cycles_done + prod_length,
        )
    merge_restart_prp("prod" + prpsuffix_liq)
    merge_restart_traj("prod" + xyzsuffix_liq)
    merge_restart_traj("prod" + Hsuffix_liq)
    if ensemble == "GEMC-NVT":
        merge_restart_prp("prod" + prpsuffix_vap)
        merge_restart_traj("prod" + xyzsuffix_vap)
        merge_restart_traj("prod" + Hsuffix_vap)